In [28]:
%%capture
!python -m nbconvert --to html Intro.ipynb --no-input

In [29]:
%%capture
!python -m nbconvert --to slides Intro.ipynb --reveal-prefix reveal.js --no-input

# Lewisham's Political Map in 2022

Lewisham's ward boundary [changes](https://consultation.lgbce.org.uk/node/17020) for the May 2022 election:

* The boundaries of 2 wards remain the same (Telegraph Hill and Forest Hill)
* 2 former wards no longer exist: New Cross and Whitefoot
* 3 new wards have been formed: Deptford, Hither Green and New Cross Gate
* 16 wards have 3 councillors
* 3 wards have only 2 councillors: Bellingham, Lewisham Central and New Cross Gate
* The total number of councillors remains at 54

_This document was produced by the Lewisham Insight & Delivery team._

## Table of Contents <a class="anchor" id="toc"></a>

<script>
    function springen(anchorId) { 
        document.getElementById(anchorId).scrollIntoView({behavior: "smooth"});
    }

    function syncScroll(source, target_ids) {
        for (let index = 0; index < target_ids.length; index++) {
            const target = document.getElementById(target_ids[index]);
            target.scrollLeft = source.scrollLeft;
        }
    }


    window.addEventListener('load', function () {
  
        const pop_all = document.querySelector('body > div:nth-child(25) > div > div.jp-OutputArea.jp-Cell-outputArea')
        pop_all.setAttribute('id','pop_all')
        pop_all.setAttribute('onScroll', 'syncScroll(this, ["pop_female", "pop_male"])')

        const pop_female = document.querySelector('body > div:nth-child(27) > div > div.jp-OutputArea.jp-Cell-outputArea')
        pop_female.setAttribute('id','pop_female')
        pop_female.setAttribute('onScroll', 'syncScroll(this, ["pop_all", "pop_male"])')

        const pop_male = document.querySelector('body > div:nth-child(29) > div > div.jp-OutputArea.jp-Cell-outputArea')
        pop_male.setAttribute('id','pop_male')
        pop_male.setAttribute('onScroll', 'syncScroll(this, ["pop_all", "pop_female"])')

    })

</script>

### <a href="#population" onclick="springen('population');">Population</a>
* <a href="#residents-per-ward" onClick="springen('residents-per-ward')">Residents per ward</a>
* <a href="#population-density" onClick="springen('population-density')">Population density</a>
* <a href="#population-by-age" onClick="springen('population-by-age')">Population by age group</a>
* <a href="#population-by-age-female" onClick="springen('population-by-age-female')">Population by age group: Female</a>
* <a href="#population-by-age-male" onClick="springen('population-by-age-male')">Population by age group: Male</a>

### <a href="#languages-spoken" onClick="springen('languages-spoken')">Languages spoken</a>
* <a href="#english-proficiency" onClick="springen('english-proficiency')">English proficiency</a>
* <a href="#other-languages" onClick="springen('other-languages')">Other languages</a>

### <a href="#country-of-birth" onClick="springen('country-of-birth')">Country of birth</a>
* <a href="#united-kingdom" onClick="springen('united-kingdom')">United kingdom</a>
* <a href="#outside-uk" onClick="springen('outside-uk')">Outside UK</a>

### <a href="#ethnicity" onClick="springen('ethnicity')">Ethnicity</a>

### <a href="#religion" onClick="springen('religion')">Religion</a>

### <a href="#qualifications" onClick="springen('qualifications')">Qualifications</a>

### <a href="#housing" onClick="springen('housing')">Housing</a>
* <a href="#accommodation" onClick="springen('accommodation')">Accommodation</a>
* <a href="#household-composition" onClick="springen('household-composition')">Household composition</a>
* <a href="#occupancy-rating" onClick="springen('occupancy-rating')">Occupancy rating</a>
* <a href="#tenure" onClick="springen('tenure')">Tenure</a>
* <a href="#car-van-availability" onClick="springen('car-van-availability')">Car/Van availability</a>
* <a href="#central-heating" onClick="springen('central-heating')">Central heating</a>

### <a href="#health" onClick="springen('health')">Health</a>
* <a href="#level-of-health" onClick="springen('level-of-health')">Level of health</a>
* <a href="#activity" onClick="springen('activity')">Activity</a>
* <a href="#unpaid-care" onClick="springen('unpaid-care')">Unpaid care</a>
* <a href="#fuel-poverty" onClick="springen('fuel-poverty')">Fuel poverty</a>

### <a href="#emplyment" onClick="springen('emplyment')">Employment</a>
* <a href="#hours-worked" onClick="springen('hours-worked')">Hours worked</a>
* <a href="#occupation-status" onClick="springen('occupation-status')">Occupation status</a>
* <a href="#occupation-groups" onClick="springen('occupation-groups')">Occupation groups</a>

### <a href="#benefits" onClick="springen('benefits')">Benefits</a>
* <a href="#female-and-male" onClick="springen('female-and-male')">Female and male</a>
* <a href="#female" onClick="springen('female')">Female</a>
* <a href="#male" onClick="springen('male')">Male</a>

### <a href="#indices-of-multiple-deprivation" onClick="springen('indices-of-multiple-deprivation')">Indices of Multiple Deprivation</a>

In [25]:
%%capture
try:
    import liad
except ImportError as e:
    %pip install git+https://github.com/lb-lewisham/liad.git

In [9]:
%%capture
try:
    import geopandas
except ImportError as e:
    %pip install geopandas

In [10]:
%%capture
try:
    import natsort
except ImportError as e:
    %pip install natsort


In [11]:
%%capture
from liad import colab
import numpy as np
import pandas as pd
import seaborn as sns
import geopandas as gpd
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
import IPython
import altair as alt
import numpy
from datetime import datetime

In [12]:
if colab.in_colab():
    from google.colab import drive
    drive.mount("/content/gdrive")
    project_dir = "/content/gdrive/MyDrive/WardProfiles"
else:    
    project_dir = "C:\\Users\\jleach\\code\\ward-profiles"

In [13]:
%%capture
import sys
sys.path.insert(1, project_dir + '/utils')

import inputs

In [14]:
%%capture
import importlib
importlib.reload(inputs)

In [15]:
lewisham = gpd.read_file(f'{project_dir}/boundaries/2022_wards/lbl_wd22.topojson')

# apply correct winding order to the polygons
from shapely.ops import orient # version >=1.7a2
lewisham.geometry = lewisham.geometry.apply(orient, args=(-1,))
lewisham.drop(columns=['id','Ward_name','OBJECTID','No_of_coun','Current_el','Forecast_e','SHAPE_Leng'], inplace=True)

In [16]:
def melted(df, id_vars, var_name, value_name):
  return (
      df
      .reset_index()
      .melt(id_vars=id_vars, var_name=var_name, value_name=value_name
    )
  )

In [17]:
def joined (gdf, df, join_on_gdf, join_on_df):
  return inputs.join_gdf_df(gdf, df,join_on_gdf, join_on_df)

In [18]:
def facet_map(df, facet, title, color_by, tooltip_title, orient="left", fmt=".2f", sort="ascending"):
  facets = df[facet].unique()
  facets = numpy.delete(facets, np.where(facets == 'index'))
  return alt.concat(*(
      alt.Chart(df[df[facet] == facet_level], title=facet_level).mark_geoshape().encode(
        color=alt.Color(color_by, legend=alt.Legend(title=title, orient=orient), sort=sort),
        tooltip=["Name:N", alt.Tooltip(facet, title=facet), alt.Tooltip(color_by, title=tooltip_title, format=fmt)]
      ).properties(
        width=200, height=200
      )
      for facet_level in facets
    ), columns=len(facets)
  )  

## Population <a class="anchor" id="population"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS, mid-2022](https://www.ons.gov.uk/file?uri=%2fpeoplepopulationandcommunity%2fpopulationandmigration%2fpopulationestimates%2fdatasets%2fcensusoutputareaestimatesinthelondonregionofengland%2fmid2020sape23dt10a/sape23dt10amid2020coaunformattedsyoaestimateslondon.xlsx)


In [219]:
df=inputs.join_gdf_df(lewisham, inputs.pop_totals, 'Name', 'Name')
df.SHAPE_Area = df.SHAPE_Area / 10000
df.loc[:, "SHAPE_Area_formatted"] = df.SHAPE_Area.map('{:,.0f}'.format)
df.rename(columns = {'SHAPE_Area_formatted':'Hectares', 'Total':'Total_INT'}, inplace = True)
df.Total_INT = df.Total_INT
df.loc[:, "Residents"] = df.Total_INT.map('{:,.0f}'.format) 
df.loc[:, "Density"] = df.Total_INT.div(df.SHAPE_Area)
df.loc[:, "Residents per Hectare"] = df.Total_INT.div(df.SHAPE_Area).map('{:,.0f}'.format) 


In [220]:
IPython.display.Markdown(f"""As of mid 2020, there were an estimated {df.sum().Total_INT:,} people living in Lewisham""")

As of mid 2020, there were an estimated 305,309 people living in Lewisham

### <a class="anchor" id="residents-per-ward">Residents per ward</a> <a onClick="springen('toc')">⬆</a>

In [221]:
alt.Chart(df).mark_geoshape().encode(
        color=alt.Color('Total_INT', sort="ascending", legend=alt.Legend(title='Residents', orient='left')),
        tooltip=["Name:N", "Residents:N"]
      ).properties(
    width=200,
    height=200
)

alt.Chart(...)

### Population density <a class="anchor" id="population-density"></a> <a onClick="springen('toc')">⬆</a>

A ward's population density is expressed here as the number of residents per Hectare

In [223]:
alt.Chart(df).mark_geoshape().encode(
color=alt.Color('Density', sort="ascending", legend=alt.Legend(
    title='Residents per Hectare', orient='left')
    ), 
    tooltip=["Name:N", "Residents:N", "Hectares:N", "Residents per Hectare:N"]
).properties(
    width=200,
    height=200
)


alt.Chart(...)

### Population by age group <a class="anchor" id="population-by-age"></a> <a onClick="springen('toc')">⬆</a>

In [84]:
df = melted(df=inputs.pop_age_groups, id_vars=['Name'], var_name='age_group', value_name='age')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='age_group', title="Percent of ward population", color_by='age:Q', tooltip_title='Percent')

alt.ConcatChart(...)

### Population by age group (female) <a class="anchor" id="population-by-age-female"></a> <a onClick="springen('toc')">⬆</a>

In [85]:
df = melted(df=inputs.pop_female, id_vars=['Name'], var_name='age_group', value_name='age')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='age_group', title="Percent of ward population", color_by='age:Q', tooltip_title='Percent')

alt.ConcatChart(...)

### Population by age group (male) <a class="anchor" id="population-by-age-male"></a> <a onClick="springen('toc')">⬆</a>

In [86]:
df = melted(df=inputs.pop_male, id_vars=['Name'], var_name='age_group', value_name='age')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='age_group', title="Percent of ward population", color_by='age:Q', tooltip_title='Percent')

alt.ConcatChart(...)

In [87]:
%%capture
import importlib
importlib.reload(inputs)

## Languages spoken <a class="anchor" id="languages-spoken"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census, 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_525_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

### English proficiency <a class="anchor" id="english-proficiency"></a> <a onClick="springen('toc')">⬆</a>

In [88]:
df = melted(df=inputs.english_proficiency[['English is main language', 'Name']], id_vars=['Name'], var_name='proficiency', value_name='language')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='proficiency', title="Percent of ward population", color_by='language:Q', tooltip_title='Percent')

alt.ConcatChart(...)

In [89]:
df = melted(df=inputs.english_proficiency[['Can speak English well or very well', 'Name']], id_vars=['Name'], var_name='proficiency', value_name='language')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='proficiency', title="Percent of ward population", color_by='language:Q', tooltip_title='Percent')

alt.ConcatChart(...)

In [90]:
df = melted(df=inputs.english_proficiency[['Cannot speak English well or at all',	'Name']], id_vars=['Name'], var_name='proficiency', value_name='language')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='proficiency', title="Percent of ward population", color_by='language:Q', tooltip_title='Percent')

alt.ConcatChart(...)

### Other languages <a class="anchor" id="other-languages"></a> <a onClick="springen('toc')">⬆</a>
The following maps show wards where more than 1% of residents speak a non-english 
language as their **main language**

In [229]:
%%capture --no-display
df = melted(df=inputs.main_language, id_vars=['Name'], var_name='main_lang', value_name='language')
df = df[df.main_lang != 'index'][(df.language>=1) & (df.language<50)]
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='main_lang', title="Percent of ward population", color_by='language:Q', tooltip_title='Percent')

alt.ConcatChart(...)

## Country of birth <a class="anchor" id="country-of-birth"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census, 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_524_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

### United Kingdom <a class="anchor" id="uk"></a> <a onClick="springen('toc')">⬆</a>

In [93]:
df = melted(df=inputs.country_of_birth.loc[:, inputs.country_of_birth.columns.str.contains('Name|United Kingdom', regex=True)], id_vars=['Name'], var_name='country', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='country', title="Residents", color_by='val:Q', tooltip_title='Count', fmt='0.0f')

alt.ConcatChart(...)

### Outside UK <a class="anchor" id="outside-uk"></a> <a onClick="springen('toc')">⬆</a>

In [94]:
df = melted(df=inputs.country_of_birth.loc[:, ~inputs.country_of_birth.columns.str.contains('Total|England|otherwise|United|Guernsey|Jersey|Isle of Man|Other', regex=True)], id_vars=['Name'], var_name='country', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='country', title="Residents in ward", color_by='val:Q', tooltip_title='Count', fmt='0.0f')

alt.ConcatChart(...)

## Ethnicity <a class="anchor" id="ethnicity"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census, 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_522_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [95]:
df = inputs.ethnicity

df = melted(df=df.loc[:, ~df.columns.str.contains('Total', regex=True)], id_vars=['Name'], var_name='Ethnicity', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Ethnicity', title="Count", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

## Religion <a class="anchor" id="religion"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_573_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [129]:
grouped = inputs.religion_groups#.groupby(by='Name', axis=0)
df = grouped
df = melted(df, id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Percent", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')

alt.ConcatChart(...)

## Qualifications <a class="anchor" id="qualifications"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_554_1.bulk.csv?time=latest&measures=20100&geography=1254112598...1254113437,1254258305,1254258306,1254258319,1254265357...1254265363,1254265589...1254265605,1254265661...1254265680,2092957699,2013265927&rural_urban=0&cell=0...7)

In [96]:
df = inputs.educational_attainment
df = melted(df=df.loc[:, ~df.columns.str.contains('Total', regex=True)], id_vars=['Name'], var_name='Qualification', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Qualification', title="Recipients in ward", color_by='val:Q', tooltip_title='Count', fmt='0.0f')


alt.ConcatChart(...)

## Housing <a class="anchor" id="housing"></a> <a onClick="springen('toc')">⬆</a>

### Accommodation <a class="anchor" id="accommodation"></a> <a onClick="springen('toc')">⬆</a>
Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_618_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [122]:
grouped = inputs.accommodation_type_groups.groupby(by='Name', axis=0)
df = grouped.mean()
df = melted(df, id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Count", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Household composition  <a class="anchor" id="household-composition"></a> <a onClick="springen('toc')">⬆</a>
Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_605_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [123]:
grouped = inputs.household_compositions_groups.groupby(by='Name', axis=0)
df = grouped.mean()
df = melted(df, id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Percent", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Occupancy rating  <a class="anchor" id="occupancy-rating"></a> <a onClick="springen('toc')">⬆</a>
Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_544_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [124]:
grouped = inputs.occupancy_rating.groupby(by='Name', axis=0)
df = grouped.mean()
df = melted(df, id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Count", color_by='val:Q', tooltip_title='Count', fmt='0.0f')


alt.ConcatChart(...)

### Tenure <a class="anchor" id="tenure"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_537_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [125]:
grouped = inputs.tenure_households.groupby(by='Name', axis=0)
df = grouped.mean()
df = df.divide(df['All categories: Tenure'], axis=0) * 100
df = melted(df=df.loc[:, ~df.columns.str.contains('All', regex=True)], id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Percent", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Car/van availability <a class="anchor" id="car-van-availability"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_621_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [230]:
grouped = inputs.car_van_availability.groupby(by='Name', axis=0)
df = grouped.mean()
df = df.div(df['All categories: Car or van availability'], axis=0)*100
df = melted(df=df.loc[:, ~df.columns.str.contains('All|sum', regex=True)], id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Percent", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Central heating <a class="anchor" id="central-heating"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_146_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

In [127]:
grouped = inputs.rooms_bedrooms_central_heating.groupby(by='Name', axis=0)
df = grouped.mean()
df['Does not have central heating'] = df['Does not have central heating'].div(df['All categories: Type of central heating in household'], axis=0) * 100
df = melted(df=df.loc[:, df.columns.str.contains('not have central heating', regex=True)], id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Percent", color_by='val:Q', tooltip_title='Percent', fmt='0.2f')


alt.ConcatChart(...)

## Health <a class="anchor" id="health"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_617_1.bulk.csv?time=latest&measures=20100&rural_urban=total&geography=2013265927TYPE299)

### Level of health <a class="anchor" id="level-of-health"></a> <a onClick="springen('toc')">⬆</a>

In [119]:
grouped = inputs.health_unpaid_care.groupby(by='Name', axis=0)
df = grouped.mean()
df = melted(df=df.loc[:, df.columns.str.contains('Health', regex=True)], id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Count", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Activity <a class="anchor" id="activity"></a> <a onClick="springen('toc')">⬆</a>

In [120]:
grouped = inputs.health_unpaid_care.groupby(by='Name', axis=0)
df = grouped.mean()
df = melted(df=df.loc[:, df.columns.str.contains('Activities Limited', regex=True)], id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Count", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Unpaid care <a class="anchor" id="unpaid-care"></a> <a onClick="springen('toc')">⬆</a>

In [121]:
grouped = inputs.health_unpaid_care.groupby(by='Name', axis=0)
df = grouped.mean()
df = melted(df=df.loc[:, df.columns.str.contains('a Week', regex=True)], id_vars=['Name'], var_name='Measure', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Measure', title="Count", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Fuel poverty <a class="anchor" id="fuel-poverty"></a> <a onClick="springen('toc')">⬆</a>

Source [Department for Business, Energy & Industrial Strategy, 2021](https://assets.publishing.service.gov.uk/government/uploads/system/uploads/attachment_data/file/981910/2021-sub-regional-fuel-poverty-tables.xlsx)


In [118]:
grouped = inputs.fuel_poverty.groupby(by='Name', axis=0)
df = grouped.mean()
df = melted(df=df.loc[:, ~df.columns.str.contains('Total|Number', regex=True)], id_vars=['Name'], var_name='Poverty', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Poverty', title="Count", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

## Employment <a class="anchor" id="employment"></a> <a onClick="springen('toc')">⬆</a>

Source [ONS Census 2011](https://www.nomisweb.co.uk/api/v01/dataset/nm_1518_1.bulk.csv?time=latest&measures=20100&geography=2013265927TYPE299)

### Hours worked <a class="anchor" id="hours-worked"></a> <a onClick="springen('toc')">⬆</a>

In [97]:
df = inputs.hours_worked

cols = df.columns[~inputs.hours_worked.columns.str.contains('Name', regex=True)]
df[cols] = df[cols].div(df['Total'], axis=0)*100

df = melted(df=df.loc[:, ~df.columns.str.contains('Total', regex=True)], id_vars=['Name'], var_name='Occupation', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Occupation', title="Count", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')


alt.ConcatChart(...)

### Occupation status <a class="anchor" id="occupation-status"></a> <a onClick="springen('toc')">⬆</a>

In [98]:
df = inputs.economic_activity
df = melted(df=df.loc[:, ~df.columns.str.contains('Total', regex=True)], id_vars=['Name'], var_name='Status', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='Status', title="Percent", color_by='val:Q', tooltip_title='Percent', fmt='0.2f')


alt.ConcatChart(...)

### Occupation groups <a class="anchor" id="occupation-groups"></a> <a onClick="springen('toc')">⬆</a>

In [99]:
def natsort_columns(columns):
  from natsort import index_natsorted
  df = pd.DataFrame(columns)
  return df.sort_values(
    by=0,
    key=lambda x: np.argsort(index_natsorted(df[0]))
  )


In [100]:
sorted_columns = natsort_columns(inputs.occupation_minor_groups.columns)
df = inputs.occupation_minor_groups.iloc[:,sorted_columns[0].index]

cols = df.columns[~df.columns.str.contains('Name', regex=True)]
df[cols] = df[cols].div(df['Total'], axis=0)*100

df.set_index('Name', inplace=True)


In [101]:
def professions(df,start,end):
  df = melted(df=df.iloc[:, start:end], id_vars=['Name'], var_name='Profession', value_name='val')
  df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
  return facet_map(df, facet='Profession', title="Percent", color_by='val:Q', tooltip_title='Percent', fmt='0.0f')

In [102]:
professions(df, 0, 9)

alt.ConcatChart(...)

In [103]:
professions(df, 10, 19)

alt.ConcatChart(...)

In [104]:
professions(df, 20, 29)

alt.ConcatChart(...)

In [105]:
professions(df, 30, 39)

alt.ConcatChart(...)

In [106]:
professions(df, 40, 49)

alt.ConcatChart(...)

In [107]:
professions(df, 50, 59)

alt.ConcatChart(...)

In [108]:
professions(df, 60, 69)

alt.ConcatChart(...)

In [109]:
professions(df, 70, 79)

alt.ConcatChart(...)

In [110]:
professions(df, 80, 89)

alt.ConcatChart(...)

In [111]:
professions(df, 90, 99)

alt.ConcatChart(...)

In [112]:
professions(df, 100, 109)

alt.ConcatChart(...)

In [113]:
professions(df, 110, 119)

alt.ConcatChart(...)

In [114]:
professions(df, 120, 124)

alt.ConcatChart(...)

## Benefits <a class="anchor" id="benefits"></a> <a onClick="springen('toc')">⬆</a>

Source DWP, Jan 2016 - Sep 2021  https://www.nomisweb.co.uk/datasets/ucjsa

_Please note: the mapping of 2011 LSOA boundaries to administrative wards is not perfectly aligned, so this data should not be considered as more than **indicative**_


#### Female and male <a class="anchor" id="female-and-male"></a> <a onClick="springen('toc')">⬆</a>

In [309]:
df = melted(df=inputs.benefits, id_vars=['Name'], var_name='Month', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
df.loc[:,'Month_datetime'] = df.Month[df.Month != 'index'].map(lambda el:datetime.strptime(el,'%B %Y'))
df = df[df.Month_datetime >= '2019-01-01']

facet_map(df, facet='Month', title="Recipients in ward", color_by='val:Q', tooltip_title='Count', fmt="0.0f")

alt.ConcatChart(...)

#### Female <a class="anchor" id="female"></a> <a onClick="springen('toc')">⬆</a>

In [310]:
df = melted(df=inputs.benefits_female, id_vars=['Name'], var_name='Month', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
df.loc[:,'Month_datetime'] = df.Month[df.Month != 'index'].map(lambda el:datetime.strptime(el,'%B %Y'))
df = df[df.Month_datetime >= '2019-01-01']
facet_map(df, facet='Month', title="Recipients in ward", color_by='val:Q', tooltip_title='Count')

alt.ConcatChart(...)

#### Male <a class="anchor" id="male"></a> <a onClick="springen('toc')">⬆</a>

In [312]:
df = melted(df=inputs.benefits_male, id_vars=['Name'], var_name='Month', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
df.loc[:,'Month_datetime'] = df.Month[df.Month != 'index'].map(lambda el:datetime.strptime(el,'%B %Y'))
df = df[df.Month_datetime >= '2019-01-01']
facet_map(df, facet='Month', title="Recipients in ward", color_by='val:Q', tooltip_title='Count')

alt.ConcatChart(...)

## Indices of Multiple Deprivation (IMD) <a class="anchor" id="indices-of-multiple-deprivation"></a> <a onClick="springen('toc')">⬆</a>

Source [Ministry of Housing, Communities & Local Government 2019](https://assets.publishing.service.gov.uk/government/uploads/system/uploads/attachment_data/file/833970/File_1_-_IMD2019_Index_of_Multiple_Deprivation.xlsx)

_Please note: the mapping of 2011 LSOA boundaries to administrative wards is not perfectly aligned, so this data should not be considered as more than **indicative**_

In [19]:
# NOTE THAT THIS IS NOT WELL SPATIALLY FITTED DATA
df = inputs.imd.groupby('Name').mean()
df = df[['IMD_decile']]
df = melted(df, id_vars=['Name'], var_name='key', value_name='val')
df = joined(lewisham, df, join_on_gdf='Name', join_on_df='Name')
facet_map(df, facet='key', title="IMD", color_by='val:Q', tooltip_title='Average decile', sort="ascending")


alt.ConcatChart(...)